In [272]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/amp-parkinsons-disease-progression-prediction/train_proteins.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/train_clinical_data.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/public_timeseries_testing_util.py
/kaggle/input/amp-parkinsons-disease-progression-prediction/supplemental_clinical_data.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/train_peptides.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/amp_pd_peptide/competition.cpython-37m-x86_64-linux-gnu.so
/kaggle/input/amp-parkinsons-disease-progression-prediction/amp_pd_peptide/__init__.py
/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test_files/sample_submission.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test_files/test_proteins.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test_files/test_peptides.csv
/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test

In [273]:
proteins = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/train_proteins.csv')
print('Proteins shape:',proteins.shape)
proteins.head()

Proteins shape: (232741, 5)


visit_id  visit_month  patient_id UniProt       NPX
0     55_0            0          55  O00391   11254.3
1     55_0            0          55  O00533  732430.0
2     55_0            0          55  O00584   39585.8
3     55_0            0          55  O14498   41526.9
4     55_0            0          55  O14773   31238.0

In [274]:
import warnings
import numpy as np
import pandas as pd

### Machine Learning ###
import xgboost as xgb
from sklearn.metrics import make_scorer
from sklearn.preprocessing import MinMaxScaler
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import KFold, cross_val_score
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

### Optimization ###
import optuna

### Viz ###
from colorama import Fore

warnings.filterwarnings('ignore')
optuna.logging.set_verbosity(optuna.logging.WARNING)

In [275]:
b_ = Fore.BLUE
c_ = Fore.CYAN
g_ = Fore.GREEN
m_ = Fore.MAGENTA
r_ = Fore.RED
y_ = Fore.YELLOW

In [276]:
def smape(actual, predicted):
    actual, predicted = np.array(actual), np.array(predicted)
    return 100/len(actual) * np.sum(2 * np.abs(predicted - actual) / (np.abs(actual) + np.abs(predicted)))

In [277]:
proteins = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/train_proteins.csv')
print('Proteins shape:',proteins.shape)
proteins.head()

Proteins shape: (232741, 5)


visit_id  visit_month  patient_id UniProt       NPX
0     55_0            0          55  O00391   11254.3
1     55_0            0          55  O00533  732430.0
2     55_0            0          55  O00584   39585.8
3     55_0            0          55  O14498   41526.9
4     55_0            0          55  O14773   31238.0

In [278]:
proteins_test = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test_files/test_proteins.csv')
print('Proteins test shape:',proteins_test.shape)
proteins_test.head()

Proteins test shape: (453, 6)


visit_id  visit_month  patient_id UniProt        NPX  group_key
0  50423_0            0       50423  O00391   33127.90          0
1  50423_0            0       50423  O00533  490742.00          0
2  50423_0            0       50423  O00584   43615.30          0
3  50423_0            0       50423  O14773   16486.60          0
4  50423_0            0       50423  O14791    2882.42          0

In [279]:
peptides = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/train_peptides.csv')
print('Peptides shape:', peptides.shape)
peptides.head()

Peptides shape: (981834, 6)


visit_id  visit_month  patient_id UniProt  \
0     55_0            0          55  O00391   
1     55_0            0          55  O00533   
2     55_0            0          55  O00533   
3     55_0            0          55  O00533   
4     55_0            0          55  O00533   

                                  Peptide  PeptideAbundance  
0                           NEQEQPLGQWHLS           11254.3  
1                             GNPEPTFSWTK          102060.0  
2                         IEIPSSVQQVPTIIK          174185.0  
3  KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK           27278.9  
4                            SMEQNGPGLEYR           30838.7

In [280]:
peptides_test = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test_files/test_peptides.csv')
print('Peptides test shape:', peptides_test.shape)
peptides_test.head()

Peptides test shape: (2057, 7)


visit_id  visit_month  patient_id UniProt  \
0  50423_0            0       50423  O00391   
1  50423_0            0       50423  O00391   
2  50423_0            0       50423  O00533   
3  50423_0            0       50423  O00533   
4  50423_0            0       50423  O00533   

                                  Peptide  PeptideAbundance  group_key  
0                    AHFSPSNIILDFPAAGSAAR           22226.3          0  
1                           NEQEQPLGQWHLS           10901.6          0  
2                             GNPEPTFSWTK           51499.4          0  
3                         IEIPSSVQQVPTIIK          125492.0          0  
4  KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK           23174.2          0

In [281]:
clinical = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/train_clinical_data.csv')
print('Clinical shape:', clinical.shape)
clinical.head()

Clinical shape: (2615, 8)


visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  \
0     55_0          55            0     10.0      6.0     15.0      NaN   
1     55_3          55            3     10.0      7.0     25.0      NaN   
2     55_6          55            6      8.0     10.0     34.0      NaN   
3     55_9          55            9      8.0      9.0     30.0      0.0   
4    55_12          55           12     10.0     10.0     41.0      0.0   

  upd23b_clinical_state_on_medication  
0                                 NaN  
1                                 NaN  
2                                 NaN  
3                                  On  
4                                  On

In [282]:
test = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/example_test_files/test.csv')
print('Test shape:', test.shape)
test.head()

Test shape: (16, 6)


visit_id  visit_month  patient_id updrs_test           row_id  group_key
0   3342_0            0        3342    updrs_1   3342_0_updrs_1          0
1   3342_0            0        3342    updrs_2   3342_0_updrs_2          0
2   3342_0            0        3342    updrs_3   3342_0_updrs_3          0
3   3342_0            0        3342    updrs_4   3342_0_updrs_4          0
4  50423_0            0       50423    updrs_1  50423_0_updrs_1          0

In [283]:
proteins.groupby('visit_id').agg({'UniProt':'nunique','patient_id':'count','NPX':['min','max','mean','std']}).reset_index()

visit_id UniProt patient_id       NPX                             \
               nunique      count       min          max          mean   
0      10053_0     165        165  2497.840  269126000.0  2.856580e+06   
1     10053_12     171        171  5800.870  270030000.0  2.728871e+06   
2     10053_18     208        208  1334.110  278835000.0  2.509967e+06   
3     10138_12     217        217  2520.240  365582000.0  3.002583e+06   
4     10138_24     219        219  1436.940  396894000.0  3.068891e+06   
...        ...     ...        ...       ...          ...           ...   
1108   8699_24     216        216   756.551  346067000.0  3.064059e+06   
1109    942_12     212        212  1722.770  330558000.0  2.613298e+06   
1110    942_24     217        217  1339.150  336769000.0  2.616142e+06   
1111    942_48     216        216  1272.480  358059000.0  2.768442e+06   
1112     942_6     216        216  2491.690  290111000.0  2.476880e+06   

                    
               std  
0     2.131630e+07  
1     2.092162e+07  
2     1.969453e+07  
3     2.516170e+07  
4     2.716806e+07  
...            ...  
1108  2.409420e+07  
1109  2.295228e+07  
1110  2.312662e+07  
1111  2.460543e+07  
1112  2.002174e+07  

[1113 rows x 7 columns]

In [401]:
df_0 = clinical[['visit_id','updrs_1']]
print('Train shape:', df_0.shape)
df_0.head()

Train shape: (2615, 2)


visit_id  updrs_1
0     55_0     10.0
1     55_3     10.0
2     55_6      8.0
3     55_9      8.0
4    55_12     10.0

In [399]:
proteinsf = proteins.groupby('visit_id').agg(NPX_min=('NPX','min'), NPX_max=('NPX','max'), NPX_mean=('NPX','mean'), NPX_std=('NPX','std'))\
                .reset_index()
proteinsf.head()

visit_id  NPX_min      NPX_max      NPX_mean       NPX_std
0   10053_0  2497.84  269126000.0  2.856580e+06  2.131630e+07
1  10053_12  5800.87  270030000.0  2.728871e+06  2.092162e+07
2  10053_18  1334.11  278835000.0  2.509967e+06  1.969453e+07
3  10138_12  2520.24  365582000.0  3.002583e+06  2.516170e+07
4  10138_24  1436.94  396894000.0  3.068891e+06  2.716806e+07

In [405]:
df_proteins = pd.merge(proteins, df_0, on = 'visit_id', how = 'inner').reset_index()
proteins_u = df_proteins.groupby('UniProt').agg(updrs_1_sum = ('updrs_1','mean')).reset_index()
proteins_u


UniProt  updrs_1_sum
0    O00391     6.152174
1    O00533     6.568885
2    O00584     6.518483
3    O14498     6.538928
4    O14773     6.560757
..      ...          ...
222  Q9UHG2     6.566479
223  Q9UKV8     6.545977
224  Q9UNU6     6.517053
225  Q9Y646     6.411706
226  Q9Y6R7     6.533000

[227 rows x 2 columns]

In [387]:
'''proteins2=proteins.drop(columns=['patient_id','UniProt'])
peptides2=peptides.drop(columns=['patient_id','UniProt','Peptide'])
p1=peptides2.groupby('visit_id').agg({'PeptideAbundance': ['min','max','mean']}).reset_index()
pr2=proteins2.groupby('visit_id').agg({'NPX':['min','max','mean']}).reset_index()
p1.columns=['visit_id','pa_min','pa_max','pa_mean']
pr2.columns=['visit_id','NPX_min','NPX_max','NPX_mean']'''

In [388]:
#pr2.columns=['visit_id','NPX_min','NPX_max','NPX_mean']

In [406]:
df_proteins = pd.merge(proteins, proteins_u, on = 'UniProt', how = 'left')
proteins_uf = df_proteins.groupby('visit_id').agg(proteins_updrs_1_min=('updrs_1_sum','min'), proteins_updrs_1_max=('updrs_1_sum','max'),\
                                                          proteins_updrs_1_mean=('updrs_1_sum','mean'), proteins_updrs_1_std=('updrs_1_sum','std'))\
                .reset_index()
proteins_uf.head()

visit_id  proteins_updrs_1_min  proteins_updrs_1_max  \
0   10053_0              6.152174              6.879464   
1  10053_12              5.981534              6.879464   
2  10053_18              5.689507              6.879464   
3  10138_12              5.689507              6.761074   
4  10138_24              5.689507              6.879464   

   proteins_updrs_1_mean  proteins_updrs_1_std  
0               6.548987              0.076462  
1               6.544246              0.088526  
2               6.527509              0.111365  
3               6.515967              0.120601  
4               6.518794              0.121644

In [407]:
s_clinical = pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/supplemental_clinical_data.csv')

In [289]:
proteins[['visit_month']].max()

visit_month    108
dtype: int64

In [290]:
peptides[['visit_month']].max()

visit_month    108
dtype: int64

In [291]:
proteins.isnull().sum()

visit_id       0
visit_month    0
patient_id     0
UniProt        0
NPX            0
dtype: int64

In [292]:
peptides.isnull().sum()

visit_id            0
visit_month         0
patient_id          0
UniProt             0
Peptide             0
PeptideAbundance    0
dtype: int64

In [293]:
clinical.isnull().sum()

visit_id                                  0
patient_id                                0
visit_month                               0
updrs_1                                   1
updrs_2                                   2
updrs_3                                  25
updrs_4                                1038
upd23b_clinical_state_on_medication    1327
dtype: int64

In [294]:
clinical.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2615 entries, 0 to 2614
Data columns (total 8 columns):
 #   Column                               Non-Null Count  Dtype  
---  ------                               --------------  -----  
 0   visit_id                             2615 non-null   object 
 1   patient_id                           2615 non-null   int64  
 2   visit_month                          2615 non-null   int64  
 3   updrs_1                              2614 non-null   float64
 4   updrs_2                              2613 non-null   float64
 5   updrs_3                              2590 non-null   float64
 6   updrs_4                              1577 non-null   float64
 7   upd23b_clinical_state_on_medication  1288 non-null   object 
dtypes: float64(4), int64(2), object(2)
memory usage: 163.6+ KB


In [295]:
test

visit_id  visit_month  patient_id updrs_test           row_id  group_key
0    3342_0            0        3342    updrs_1   3342_0_updrs_1          0
1    3342_0            0        3342    updrs_2   3342_0_updrs_2          0
2    3342_0            0        3342    updrs_3   3342_0_updrs_3          0
3    3342_0            0        3342    updrs_4   3342_0_updrs_4          0
4   50423_0            0       50423    updrs_1  50423_0_updrs_1          0
5   50423_0            0       50423    updrs_2  50423_0_updrs_2          0
6   50423_0            0       50423    updrs_3  50423_0_updrs_3          0
7   50423_0            0       50423    updrs_4  50423_0_updrs_4          0
8    3342_6            6        3342    updrs_1   3342_6_updrs_1          6
9    3342_6            6        3342    updrs_2   3342_6_updrs_2          6
10   3342_6            6        3342    updrs_3   3342_6_updrs_3          6
11   3342_6            6        3342    updrs_4   3342_6_updrs_4          6
12  50423_6            6       50423    updrs_1  50423_6_updrs_1          6
13  50423_6            6       50423    updrs_2  50423_6_updrs_2          6
14  50423_6            6       50423    updrs_3  50423_6_updrs_3          6
15  50423_6            6       50423    updrs_4  50423_6_updrs_4          6

In [296]:
peptides

visit_id  visit_month  patient_id UniProt  \
0            55_0            0          55  O00391   
1            55_0            0          55  O00533   
2            55_0            0          55  O00533   
3            55_0            0          55  O00533   
4            55_0            0          55  O00533   
...           ...          ...         ...     ...   
981829  58648_108          108       58648  Q9UHG2   
981830  58648_108          108       58648  Q9UKV8   
981831  58648_108          108       58648  Q9Y646   
981832  58648_108          108       58648  Q9Y6R7   
981833  58648_108          108       58648  Q9Y6R7   

                                       Peptide  PeptideAbundance  
0                                NEQEQPLGQWHLS          11254.30  
1                                  GNPEPTFSWTK         102060.00  
2                              IEIPSSVQQVPTIIK         174185.00  
3       KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK          27278.90  
4                                 SMEQNGPGLEYR          30838.70  
...                                        ...               ...  
981829                         ILAGSADSEGVAAPR         202820.00  
981830                           SGNIPAGTTVDTK         105830.00  
981831                             LALLVDTVGPR          21257.60  
981832        AGC(UniMod_4)VAESTAVC(UniMod_4)R           5127.26  
981833                          GATTSPGVYELSSR          12825.90  

[981834 rows x 6 columns]

In [297]:
proteins

visit_id  visit_month  patient_id UniProt       NPX
0            55_0            0          55  O00391   11254.3
1            55_0            0          55  O00533  732430.0
2            55_0            0          55  O00584   39585.8
3            55_0            0          55  O14498   41526.9
4            55_0            0          55  O14773   31238.0
...           ...          ...         ...     ...       ...
232736  58648_108          108       58648  Q9UBX5   27387.8
232737  58648_108          108       58648  Q9UHG2  369437.0
232738  58648_108          108       58648  Q9UKV8  105830.0
232739  58648_108          108       58648  Q9Y646   21257.6
232740  58648_108          108       58648  Q9Y6R7   17953.1

[232741 rows x 5 columns]

In [298]:
clinical.value_counts()

visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  upd23b_clinical_state_on_medication
10138_0   10138       0            8.0      6.0      15.0     0.0      On                                     1
51846_18  51846       18           8.0      4.0      9.0      0.0      On                                     1
51879_0   51879       0            2.0      8.0      47.0     0.0      Off                                    1
51846_6   51846       6            8.0      2.0      8.0      0.0      On                                     1
51846_48  51846       48           5.0      1.0      12.0     2.0      Off                                    1
                                                                                                             ..
27893_30  27893       30           11.0     15.0     27.0     0.0      On                                     1
27893_24  27893       24           7.0      15.0     27.0     0.0      On                                    

In [299]:
c2= pd.read_csv('/kaggle/input/amp-parkinsons-disease-progression-prediction/supplemental_clinical_data.csv')

In [300]:
proteins[['patient_id']].value_counts()

patient_id
62723         1929
20404         1924
23391         1919
26210         1912
18183         1899
              ... 
55240          429
42086          427
25911          419
52119          417
41930          199
Length: 248, dtype: int64

In [301]:
peptides[['patient_id']].value_counts()

patient_id
20404         8272
23391         8147
62723         8111
26210         8076
18183         7965
              ... 
55240         1810
52119         1804
25911         1782
42086         1781
41930          876
Length: 248, dtype: int64

In [302]:
proteins[['visit_month']].value_counts()

visit_month
0              40587
12             37467
24             36225
36             31156
48             28838
6              25991
60             17572
84              6288
72              4407
18              1657
108              855
3                641
96               423
54               418
30               216
dtype: int64

In [303]:
clinical[['patient_id']].value_counts()

patient_id
55096         17
57108         17
15009         17
16778         16
52266         16
              ..
13968          5
20792          5
62732          4
60443          3
14450          3
Length: 248, dtype: int64

In [304]:
c2[['patient_id']].value_counts()

patient_id
12956         6
58377         6
8614          6
57367         6
9251          6
             ..
53143         1
53241         1
40776         1
12732         1
34311         1
Length: 771, dtype: int64

In [306]:
c2.columns=clinical.columns

In [307]:
all_clinical=pd.concat([clinical,c2])

In [308]:
all_clinical

visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  \
0         55_0          55            0     10.0      6.0     15.0      NaN   
1         55_3          55            3     10.0      7.0     25.0      NaN   
2         55_6          55            6      8.0     10.0     34.0      NaN   
3         55_9          55            9      8.0      9.0     30.0      0.0   
4        55_12          55           12     10.0     10.0     41.0      0.0   
...        ...         ...          ...      ...      ...      ...      ...   
2218   65382_0       65382            0      NaN      NaN      0.0      NaN   
2219   65405_0       65405            0      5.0     16.0     31.0      0.0   
2220   65405_5       65405            5      NaN      NaN     57.0      NaN   
2221   65530_0       65530            0     10.0      6.0     24.0      0.0   
2222  65530_36       65530           36      8.0      4.0     15.0      4.0   

     upd23b_clinical_state_on_medication  
0                                    NaN  
1                                    NaN  
2                                    NaN  
3                                     On  
4                                     On  
...                                  ...  
2218                                 NaN  
2219                                 NaN  
2220                                 NaN  
2221                                 NaN  
2222                                  On  

[4838 rows x 8 columns]

In [309]:
all_clinical2=all_clinical
all_clinical2['upd23b_clinical_state_on_medication']=all_clinical[['upd23b_clinical_state_on_medication']].fillna('Off')
all_clinical2['updrs_4']=all_clinical[['updrs_4']].fillna(0)

In [409]:
peptides_f = peptides.groupby('visit_id').agg(Abe_min=('PeptideAbundance','min'), Abe_max=('PeptideAbundance','max'),\
                                                                Abe_mean=('PeptideAbundance','mean'), Abe_std=('PeptideAbundance','std'))\
                .reset_index()
peptides_f

visit_id   Abe_min      Abe_max       Abe_mean       Abe_std
0      10053_0   82.9679   66333900.0  726248.393431  3.535602e+06
1     10053_12  128.4460   73059300.0  737183.385744  3.799654e+06
2     10053_18  108.5000   64711200.0  601466.784320  3.006568e+06
3     10138_12  129.0240   71652400.0  699099.199189  3.379573e+06
4     10138_24  142.6480  123897000.0  732120.888877  4.912602e+06
...        ...       ...          ...            ...           ...
1108   8699_24  106.9420   99846400.0  726494.824901  4.080307e+06
1109    942_12   88.3277   70888500.0  623193.979635  3.362987e+06
1110    942_24  108.7050   71995500.0  623849.652027  3.294163e+06
1111    942_48  148.1360   70658500.0  659297.802601  3.359265e+06
1112     942_6  158.8690   58472500.0  582795.558517  2.734257e+06

[1113 rows x 5 columns]

In [425]:
all_clinical3=pd.get_dummies(all_clinical2,columns=['upd23b_clinical_state_on_medication'])
all_clinical3

visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  \
0         55_0          55            0     10.0      6.0     15.0      0.0   
1         55_3          55            3     10.0      7.0     25.0      0.0   
2         55_6          55            6      8.0     10.0     34.0      0.0   
3         55_9          55            9      8.0      9.0     30.0      0.0   
4        55_12          55           12     10.0     10.0     41.0      0.0   
...        ...         ...          ...      ...      ...      ...      ...   
2218   65382_0       65382            0      NaN      NaN      0.0      0.0   
2219   65405_0       65405            0      5.0     16.0     31.0      0.0   
2220   65405_5       65405            5      NaN      NaN     57.0      0.0   
2221   65530_0       65530            0     10.0      6.0     24.0      0.0   
2222  65530_36       65530           36      8.0      4.0     15.0      4.0   

      upd23b_clinical_state_on_medication_Off  \
0                                           1   
1                                           1   
2                                           1   
3                                           0   
4                                           0   
...                                       ...   
2218                                        1   
2219                                        1   
2220                                        1   
2221                                        1   
2222                                        0   

      upd23b_clinical_state_on_medication_On  
0                                          0  
1                                          0  
2                                          0  
3                                          1  
4                                          1  
...                                      ...  
2218                                       0  
2219                                       0  
2220                                       0  
2221                                       0  
2222                                       1  

[4838 rows x 9 columns]

In [410]:
df_peptides = pd.merge(peptides, df_0, on = 'visit_id', how = 'inner').reset_index()
peptides_u = df_peptides.groupby('Peptide').agg(updrs_1_sum = ('updrs_1','mean')).reset_index()
peptides_u.head()

Peptide  updrs_1_sum
0                                     AADDTWEPFASGK     6.600976
1  AAFGQGSGPIMLDEVQC(UniMod_4)TGTEASLADC(UniMod_4)K     6.593625
2                  AAFTEC(UniMod_4)C(UniMod_4)QAADK     6.575729
3                                       AANEVSSADVK     6.573563
4                           AATGEC(UniMod_4)TATVGKR     6.511416

In [312]:
peptides[peptides['Peptide']=='GLVSWGNIPC(UniMod_4)GSK']

visit_id  visit_month  patient_id UniProt                  Peptide  \
899          55_0            0          55  Q92876  GLVSWGNIPC(UniMod_4)GSK   
1802       1517_0            0        1517  Q92876  GLVSWGNIPC(UniMod_4)GSK   
2680       1923_0            0        1923  Q92876  GLVSWGNIPC(UniMod_4)GSK   
3587       2660_0            0        2660  Q92876  GLVSWGNIPC(UniMod_4)GSK   
4467       3636_0            0        3636  Q92876  GLVSWGNIPC(UniMod_4)GSK   
...           ...          ...         ...     ...                      ...   
978172   58648_96           96       58648  Q92876  GLVSWGNIPC(UniMod_4)GSK   
979063   5645_108          108        5645  Q92876  GLVSWGNIPC(UniMod_4)GSK   
979973  12703_108          108       12703  Q92876  GLVSWGNIPC(UniMod_4)GSK   
980895  55096_108          108       55096  Q92876  GLVSWGNIPC(UniMod_4)GSK   
981801  58648_108          108       58648  Q92876  GLVSWGNIPC(UniMod_4)GSK   

        PeptideAbundance  
899             724168.0  
1802            606324.0  
2680           1161040.0  
3587            808147.0  
4467            330256.0  
...                  ...  
978172          464939.0  
979063          777961.0  
979973          755370.0  
980895          415757.0  
981801          588372.0  

[1097 rows x 6 columns]

In [313]:
proteins[proteins['UniProt']=='P07333']

visit_id  visit_month  patient_id UniProt      NPX
96           55_0            0          55  P07333  54219.0
315        1517_0            0        1517  P07333  31639.9
524        1923_0            0        1923  P07333  43414.7
735        2660_0            0        2660  P07333  74919.3
945        3636_0            0        3636  P07333  45944.4
...           ...          ...         ...     ...      ...
231557    5645_96           96        5645  P07333  25904.0
231766   58648_96           96       58648  P07333  33764.0
231979   5645_108          108        5645  P07333  20807.3
232193  12703_108          108       12703  P07333  46080.7
232622  58648_108          108       58648  P07333  50734.1

[923 rows x 5 columns]

In [411]:
df_peptides = pd.merge(peptides, peptides_u, on = 'Peptide', how = 'left')
peptides_ft = df_peptides.groupby('visit_id').agg(peptides_updrs_1_min=('updrs_1_sum','min'), peptides_updrs_1_max=('updrs_1_sum','max'),\
                                                          peptides_updrs_1_mean=('updrs_1_sum','mean'), peptides_updrs_1_std=('updrs_1_sum','std'))\
                .reset_index()
peptides_ft


visit_id  peptides_updrs_1_min  peptides_updrs_1_max  \
0      10053_0              6.049037              6.906049   
1     10053_12              5.981534              6.906049   
2     10053_18              5.689507              6.962025   
3     10138_12              5.689507              6.906049   
4     10138_24              5.689507              6.962025   
...        ...                   ...                   ...   
1108   8699_24              5.760582              6.962025   
1109    942_12              5.760582              6.906049   
1110    942_24              5.760582              6.962025   
1111    942_48              5.760582              6.962025   
1112     942_6              5.689507              6.962025   

      peptides_updrs_1_mean  peptides_updrs_1_std  
0                  6.527529              0.078700  
1                  6.525244              0.083481  
2                  6.514714              0.098449  
3                  6.500814              0.112576  
4                  6.504425              0.109622  
...                     ...                   ...  
1108               6.504196              0.107415  
1109               6.507013              0.100552  
1110               6.503268              0.104013  
1111               6.501995              0.104053  
1112               6.503208              0.109613  

[1113 rows x 5 columns]

In [412]:
df_0_1 = clinical[['visit_id','updrs_1']]
df_0_2 = clinical[['visit_id','updrs_2']]
df_0_3 = clinical[['visit_id','updrs_3']]
df_0_4 = clinical[['visit_id','updrs_4']]

df_proteins = pd.merge(proteins, df_0_1, on = 'visit_id', how = 'inner').reset_index()
proteins_Uniprot_updrs1 = df_proteins.groupby('UniProt').agg(updrs_1_sum = ('updrs_1','mean')).reset_index()

df_proteins = pd.merge(proteins, df_0_2, on = 'visit_id', how = 'inner').reset_index()
proteins_Uniprot_updrs2 = df_proteins.groupby('UniProt').agg(updrs_1_sum = ('updrs_2','mean')).reset_index()

df_proteins = pd.merge(proteins, df_0_3, on = 'visit_id', how = 'inner').reset_index()
proteins_Uniprot_updrs3 = df_proteins.groupby('UniProt').agg(updrs_1_sum = ('updrs_3','mean')).reset_index()

df_proteins = pd.merge(proteins, df_0_4, on = 'visit_id', how = 'inner').reset_index()
proteins_Uniprot_updrs4 = df_proteins.groupby('UniProt').agg(updrs_1_sum = ('updrs_4','mean')).reset_index()

df_peptides = pd.merge(peptides, df_0_1, on = 'visit_id', how = 'inner').reset_index()
peptides_PeptideAbundance_updrs1 = df_peptides.groupby('Peptide').agg(updrs_1_sum = ('updrs_1','mean')).reset_index()

df_peptides = pd.merge(peptides, df_0_2, on = 'visit_id', how = 'inner').reset_index()
peptides_PeptideAbundance_updrs2 = df_peptides.groupby('Peptide').agg(updrs_1_sum = ('updrs_2','mean')).reset_index()

df_peptides = pd.merge(peptides, df_0_3, on = 'visit_id', how = 'inner').reset_index()
peptides_PeptideAbundance_updrs3 = df_peptides.groupby('Peptide').agg(updrs_1_sum = ('updrs_3','mean')).reset_index()

df_peptides = pd.merge(peptides, df_0_4, on = 'visit_id', how = 'inner').reset_index()
peptides_PeptideAbundance_updrs4 = df_peptides.groupby('Peptide').agg(updrs_1_sum = ('updrs_4','mean')).reset_index()

df_proteins_fts = [proteins_Uniprot_updrs1, proteins_Uniprot_updrs2, proteins_Uniprot_updrs3, proteins_Uniprot_updrs4]
df_peptides_fts = [peptides_PeptideAbundance_updrs1, peptides_PeptideAbundance_updrs2, peptides_PeptideAbundance_updrs3, peptides_PeptideAbundance_updrs4]
df_lst = [df_0_1, df_0_2, df_0_3, df_0_4]

In [423]:
def features(df, proteins, peptides, classes):
    proteins_npx_ft = proteins.groupby('visit_id').agg(NPX_min=('NPX','min'), NPX_max=('NPX','max'), NPX_mean=('NPX','mean'), NPX_std=('NPX','std'))\
                    .reset_index()
    peptides_PeptideAbundance_ft = peptides.groupby('visit_id').agg(Abe_min=('PeptideAbundance','min'), Abe_max=('PeptideAbundance','max'),\
                                                                    Abe_mean=('PeptideAbundance','mean'), Abe_std=('PeptideAbundance','std'))\
                    .reset_index()

    df_proteins = pd.merge(proteins, df_proteins_fts[classes], on = 'UniProt', how = 'left')
    proteins_UniProt_ft = df_proteins.groupby('visit_id').agg(proteins_updrs_1_min=('updrs_1_sum','min'), proteins_updrs_1_max=('updrs_1_sum','max'),\
                                                              proteins_updrs_1_mean=('updrs_1_sum','mean'), proteins_updrs_1_std=('updrs_1_sum','std'))\
                    .reset_index()
    df_peptides = pd.merge(peptides, df_peptides_fts[classes], on = 'Peptide', how = 'left')
    peptides_ft = df_peptides.groupby('visit_id').agg(peptides_updrs_1_min=('updrs_1_sum','min'), peptides_updrs_1_max=('updrs_1_sum','max'),\
                                                              peptides_updrs_1_mean=('updrs_1_sum','mean'), peptides_updrs_1_std=('updrs_1_sum','std'))\
                    .reset_index()

    df = pd.merge(df, proteins_npx_ft, on = 'visit_id', how = 'left')
    df = pd.merge(df, peptides_PeptideAbundance_ft, on = 'visit_id', how = 'left')
    df = pd.merge(df, proteins_UniProt_ft, on = 'visit_id', how = 'left')
    df = pd.merge(df, peptides_ft, on = 'visit_id', how = 'left')
    df = df.fillna(df.mean())
    return df

In [424]:
train_0 = features(df_0_1, proteins, peptides, 0)
train_0

visit_id  updrs_1      NPX_min       NPX_max      NPX_mean  \
0         55_0     10.0  3417.710000  3.902390e+08  3.180508e+06   
1         55_3     10.0  1919.833074  3.105057e+08  2.709039e+06   
2         55_6      8.0  2505.100000  3.475720e+08  2.942039e+06   
3         55_9      8.0  1919.833074  3.105057e+08  2.709039e+06   
4        55_12     10.0  3592.520000  3.835070e+08  3.145608e+06   
...        ...      ...          ...           ...           ...   
2610  65043_48      7.0  3137.070000  3.066470e+08  2.917391e+06   
2611  65043_54      4.0  1919.833074  3.105057e+08  2.709039e+06   
2612  65043_60      6.0  1919.833074  3.105057e+08  2.709039e+06   
2613  65043_72      3.0  1919.833074  3.105057e+08  2.709039e+06   
2614  65043_84      7.0  1919.833074  3.105057e+08  2.709039e+06   

           NPX_std      Abe_min       Abe_max       Abe_mean       Abe_std  \
0     2.672700e+07  2148.350000  9.970120e+07  748153.907014  4.231806e+06   
1     2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2     2.391469e+07  1444.290000  7.759770e+07  685218.599872  3.491859e+06   
3     2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
4     2.612674e+07  2814.330000  8.651350e+07  740535.423563  3.882536e+06   
...            ...          ...           ...            ...           ...   
2610  2.171818e+07   117.149000  6.498220e+07  669411.457384  3.243698e+06   
2611  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2612  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2613  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2614  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   

      proteins_updrs_1_min  proteins_updrs_1_max  proteins_updrs_1_mean  \
0                 5.936858              6.879464               6.515501   
1                 5.855558              6.829984               6.522686   
2                 5.936858              6.879464               6.516485   
3                 5.855558              6.829984               6.522686   
4                 5.689507              6.761074               6.509822   
...                    ...                   ...                    ...   
2610              5.689507              6.761074               6.513409   
2611              5.855558              6.829984               6.522686   
2612              5.855558              6.829984               6.522686   
2613              5.855558              6.829984               6.522686   
2614              5.855558              6.829984               6.522686   

      proteins_updrs_1_std  peptides_updrs_1_min  peptides_updrs_1_max  \
0                 0.117316              5.760582              6.906049   
1                 0.108527              5.765975              6.931777   
2                 0.117584              5.760582              6.962025   
3                 0.108527              5.765975              6.931777   
4                 0.127918              5.689507              6.962025   
...                    ...                   ...                   ...   
2610              0.124300              5.689507              6.906049   
2611              0.108527              5.765975              6.931777   
2612              0.108527              5.765975              6.931777   
2613              0.108527              5.765975              6.931777   
2614              0.108527              5.765975              6.931777   

      peptides_updrs_1_mean  peptides_updrs_1_std  
0                  6.499588              0.113166  
1                  6.506576              0.103863  
2                  6.501296              0.110881  
3                  6.506576              0.103863  
4                  6.498244              0.116800  
...                     ...                   ...  
2610               6.501298              0.111167  
2611               6.506576              0.103

In [427]:
train00=pd.merge(train_0,all_clinical3,on='visit_id')
train00

visit_id  updrs_1_x      NPX_min       NPX_max      NPX_mean  \
0         55_0       10.0  3417.710000  3.902390e+08  3.180508e+06   
1         55_3       10.0  1919.833074  3.105057e+08  2.709039e+06   
2         55_6        8.0  2505.100000  3.475720e+08  2.942039e+06   
3         55_9        8.0  1919.833074  3.105057e+08  2.709039e+06   
4        55_12       10.0  3592.520000  3.835070e+08  3.145608e+06   
...        ...        ...          ...           ...           ...   
2610  65043_48        7.0  3137.070000  3.066470e+08  2.917391e+06   
2611  65043_54        4.0  1919.833074  3.105057e+08  2.709039e+06   
2612  65043_60        6.0  1919.833074  3.105057e+08  2.709039e+06   
2613  65043_72        3.0  1919.833074  3.105057e+08  2.709039e+06   
2614  65043_84        7.0  1919.833074  3.105057e+08  2.709039e+06   

           NPX_std      Abe_min       Abe_max       Abe_mean       Abe_std  \
0     2.672700e+07  2148.350000  9.970120e+07  748153.907014  4.231806e+06   
1     2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2     2.391469e+07  1444.290000  7.759770e+07  685218.599872  3.491859e+06   
3     2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
4     2.612674e+07  2814.330000  8.651350e+07  740535.423563  3.882536e+06   
...            ...          ...           ...            ...           ...   
2610  2.171818e+07   117.149000  6.498220e+07  669411.457384  3.243698e+06   
2611  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2612  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2613  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2614  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   

      ...  peptides_updrs_1_mean  peptides_updrs_1_std  patient_id  \
0     ...               6.499588              0.113166          55   
1     ...               6.506576              0.103863          55   
2     ...               6.501296              0.110881          55   
3     ...               6.506576              0.103863          55   
4     ...               6.498244              0.116800          55   
...   ...                    ...                   ...         ...   
2610  ...               6.501298              0.111167       65043   
2611  ...               6.506576              0.103863       65043   
2612  ...               6.506576              0.103863       65043   
2613  ...               6.506576              0.103863       65043   
2614  ...               6.506576              0.103863       65043   

      visit_month  updrs_1_y  updrs_2  updrs_3  updrs_4  \
0               0       10.0      6.0     15.0      0.0   
1               3       10.0      7.0     25.0      0.0   
2               6        8.0     10.0     34.0      0.0   
3               9        8.0      9.0     30.0      0.0   
4              12       10.0     10.0     41.0      0.0   
...           ...        ...      ...      ...      ...   
2610           48        7.0      6.0     13.0      0.0   
2611           54        4.0      8.0     11.0      1.0   
2612           60        6.0      6.0     16.0      1.0   
2613           72        3.0      9.0     14.0      1.0   
2614           84        7.0      9.0     20.0      3.0   

      upd23b_clinical_state_on_medication_Off  \
0                                           1   
1                                           1   
2                                           1   
3                                           0   
4                                           0   
...                                       ...   
2610                                        1   
2611                                        1   
2612                                        1   
2613                                        1   
2614                                        1   

      upd23b_clinical_state_on_medication_On  
0                                         

In [316]:
train_all3=train_all2.dropna()

In [429]:
import pandas as pd

from sklearn.ensemble import RandomForestRegressor

from sklearn.model_selection import train_test_split

from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

from sklearn import metrics
from sklearn.metrics import r2_score, mean_squared_error, make_scorer

from sklearn.metrics import confusion_matrix,precision_score,recall_score,classification_report, accuracy_score
from sklearn.model_selection import StratifiedKFold, KFold
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import MinMaxScaler
import warnings

warnings.filterwarnings('ignore')

In [430]:
model = {}
mms = MinMaxScaler()
n_estimators = [5,20,50,100] # number of trees in the random forest
max_features = ['auto', 'sqrt'] # number of features in consideration at every split
max_depth = [int(x) for x in np.linspace(10, 120, num = 12)] # maximum number of levels allowed in each decision tree
min_samples_split = [2, 6, 10] # minimum sample number to split a node
min_samples_leaf = [1, 3, 4] # minimum sample number that can be stored in a leaf node
bootstrap = [True, False] # method used to sample data points


for i in range(3):
    print('--------------------------------------------------------')
    print('Model {0}'.format(i + 1))
    train_0 = features(df_lst[i], proteins, peptides, i)
    scale_col = ['NPX_min','NPX_max','NPX_mean','NPX_std', 'Abe_min', 'Abe_max', 'Abe_mean', 'Abe_std']
    train_0[scale_col] = mms.fit_transform(train_0[scale_col])
    
    rfc = RandomForestRegressor()
    forest_params = [{'n_estimators': n_estimators,

    'max_features': max_features,

    'max_depth': max_depth,

    'min_samples_split': min_samples_split,

    'min_samples_leaf': min_samples_leaf,

    'bootstrap': bootstrap}]
    cv = KFold(n_splits=10, shuffle=True, random_state=42)
    clf = RandomizedSearchCV(rfc, forest_params, cv = cv, scoring=make_scorer(smape), verbose = -1)
    
    X = train_0.drop(columns = ['visit_id','updrs_{0}'.format(i + 1)], axis = 1)
    y = train_0['updrs_{0}'.format(i + 1)].astype(np.float32)
    clf.fit(X, y)

    print(clf.best_params_)

    print(clf.best_score_)
    print('Train smape:',smape(train_0['updrs_{0}'.format(i + 1)], clf.predict(train_0.drop(columns = ['visit_id','updrs_{0}'.format(i + 1)], axis = 1))))
    model[i] = clf

--------------------------------------------------------
Model 1
{'n_estimators': 100, 'min_samples_split': 6, 'min_samples_leaf': 1, 'max_features': 'auto', 'max_depth': 30, 'bootstrap': False}
73.24898329739041
Train smape: 49.69032300342345
--------------------------------------------------------
Model 2
{'n_estimators': 5, 'min_samples_split': 2, 'min_samples_leaf': 3, 'max_features': 'auto', 'max_depth': 90, 'bootstrap': False}
95.43513150859674
Train smape: 69.39306490612711
--------------------------------------------------------
Model 3
{'n_estimators': 5, 'min_samples_split': 10, 'min_samples_leaf': 1, 'max_features': 'auto', 'max_depth': 80, 'bootstrap': True}
76.86195338240509
Train smape: 67.83052150420623


In [317]:
train_all3.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1058 entries, 0 to 2610
Data columns (total 15 columns):
 #   Column                                   Non-Null Count  Dtype  
---  ------                                   --------------  -----  
 0   visit_id                                 1058 non-null   object 
 1   NPX_min                                  1058 non-null   float64
 2   NPX_max                                  1058 non-null   float64
 3   NPX_mean                                 1058 non-null   float64
 4   pa_min                                   1058 non-null   float64
 5   pa_max                                   1058 non-null   float64
 6   pa_mean                                  1058 non-null   float64
 7   patient_id                               1058 non-null   int64  
 8   visit_month                              1058 non-null   int64  
 9   updrs_1                                  1058 non-null   float64
 10  updrs_2                                  1058 no

In [433]:
train00.head()


visit_id  updrs_1_x      NPX_min       NPX_max      NPX_mean       NPX_std  \
0     55_0       10.0  3417.710000  3.902390e+08  3.180508e+06  2.672700e+07   
1     55_3       10.0  1919.833074  3.105057e+08  2.709039e+06  2.187820e+07   
2     55_6        8.0  2505.100000  3.475720e+08  2.942039e+06  2.391469e+07   
3     55_9        8.0  1919.833074  3.105057e+08  2.709039e+06  2.187820e+07   
4    55_12       10.0  3592.520000  3.835070e+08  3.145608e+06  2.612674e+07   

       Abe_min       Abe_max       Abe_mean       Abe_std  ...  \
0  2148.350000  9.970120e+07  748153.907014  4.231806e+06  ...   
1   202.807182  7.132767e+07  643824.665882  3.321411e+06  ...   
2  1444.290000  7.759770e+07  685218.599872  3.491859e+06  ...   
3   202.807182  7.132767e+07  643824.665882  3.321411e+06  ...   
4  2814.330000  8.651350e+07  740535.423563  3.882536e+06  ...   

   peptides_updrs_1_mean  peptides_updrs_1_std  patient_id  visit_month  \
0               6.499588              0.113166          55            0   
1               6.506576              0.103863          55            3   
2               6.501296              0.110881          55            6   
3               6.506576              0.103863          55            9   
4               6.498244              0.116800          55           12   

   updrs_1_y  updrs_2  updrs_3  updrs_4  \
0       10.0      6.0     15.0      0.0   
1       10.0      7.0     25.0      0.0   
2        8.0     10.0     34.0      0.0   
3        8.0      9.0     30.0      0.0   
4       10.0     10.0     41.0      0.0   

   upd23b_clinical_state_on_medication_Off  \
0                                        1   
1                                        1   
2                                        1   
3                                        0   
4                                        0   

   upd23b_clinical_state_on_medication_On  
0                                       0  
1                                       0  
2                                       0  
3                                       1  
4                                       1  

[5 rows x 26 columns]

In [477]:
featuresall=train00.columns.difference(['visit_id','patient_id','upd23b_clinical_state_on_medication_Off','upd23b_clinical_state_on_medication_On','updrs_1_x','updrs_2','updrs_3','updrs_4'])
features0=train00.columns.difference(['visit_id','patient_id','updrs_1','updrs_2','updrs_3','updrs_4'])
features1=train00.columns.difference(['visit_id','patient_id','updrs_1','updrs_2','updrs_3','updrs_4'])
features2=train00.columns.difference(['updrs_1','updrs_2','updrs_3','updrs_4','visit_id','patient_id'])
features3=train00.columns.difference(['visit_id','patient_id','updrs_1','updrs_2','updrs_3','updrs_4'])
features_1=train00.columns.difference(['visit_id','patient_id','updrs_4'])


In [478]:
train00

visit_id  updrs_1_x      NPX_min       NPX_max      NPX_mean  \
0         55_0       10.0  3417.710000  3.902390e+08  3.180508e+06   
1         55_3       10.0  1919.833074  3.105057e+08  2.709039e+06   
2         55_6        8.0  2505.100000  3.475720e+08  2.942039e+06   
3         55_9        8.0  1919.833074  3.105057e+08  2.709039e+06   
4        55_12       10.0  3592.520000  3.835070e+08  3.145608e+06   
...        ...        ...          ...           ...           ...   
2610  65043_48        7.0  3137.070000  3.066470e+08  2.917391e+06   
2611  65043_54        4.0  1919.833074  3.105057e+08  2.709039e+06   
2612  65043_60        6.0  1919.833074  3.105057e+08  2.709039e+06   
2613  65043_72        3.0  1919.833074  3.105057e+08  2.709039e+06   
2614  65043_84        7.0  1919.833074  3.105057e+08  2.709039e+06   

           NPX_std      Abe_min       Abe_max       Abe_mean       Abe_std  \
0     2.672700e+07  2148.350000  9.970120e+07  748153.907014  4.231806e+06   
1     2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2     2.391469e+07  1444.290000  7.759770e+07  685218.599872  3.491859e+06   
3     2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
4     2.612674e+07  2814.330000  8.651350e+07  740535.423563  3.882536e+06   
...            ...          ...           ...            ...           ...   
2610  2.171818e+07   117.149000  6.498220e+07  669411.457384  3.243698e+06   
2611  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2612  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2613  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   
2614  2.187820e+07   202.807182  7.132767e+07  643824.665882  3.321411e+06   

      ...  peptides_updrs_1_max  peptides_updrs_1_mean  peptides_updrs_1_std  \
0     ...              6.906049               6.499588              0.113166   
1     ...              6.931777               6.506576              0.103863   
2     ...              6.962025               6.501296              0.110881   
3     ...              6.931777               6.506576              0.103863   
4     ...              6.962025               6.498244              0.116800   
...   ...                   ...                    ...                   ...   
2610  ...              6.906049               6.501298              0.111167   
2611  ...              6.931777               6.506576              0.103863   
2612  ...              6.931777               6.506576              0.103863   
2613  ...              6.931777               6.506576              0.103863   
2614  ...              6.931777               6.506576              0.103863   

      patient_id  visit_month  updrs_2  updrs_3  updrs_4  \
0             55            0      6.0     15.0      0.0   
1             55            3      7.0     25.0      0.0   
2             55            6     10.0     34.0      0.0   
3             55            9      9.0     30.0      0.0   
4             55           12     10.0     41.0      0.0   
...          ...          ...      ...      ...      ...   
2610       65043           48      6.0     13.0      0.0   
2611       65043           54      8.0     11.0      1.0   
2612       65043           60      6.0     16.0      1.0   
2613       65043           72      9.0     14.0      1.0   
2614       65043           84      9.0     20.0      3.0   

      upd23b_clinical_state_on_medication_Off  \
0                                           1   
1                                           1   
2                                           1   
3                                           0   
4                                           0   
...                                       ...   
2610                                        1   
2611                                        1   
2612                                        1   
2613                                        1   
2614   

In [461]:
# Robust scaling 수행
#scaler = RobustScaler()
#train_all32 = scaler.fit_transform(train_all3[features2.tolist()])
#train_all322 = pd.DataFrame(train_all32,columns=features2)
#train_all33 = scaler.fit_transform(train_all3[features3.tolist()])
#train_all333 = pd.DataFrame(train_all33,columns=features3)
#train_all3_1 = scaler.fit_transform(train_all3[features_1.tolist()])
#train_all3_11 = pd.DataFrame(train_all3_1,columns=features_1)
#train_all34 = scaler.fit_transform(train_all3[features4.tolist()])
#train_all344 = pd.DataFrame(train_all34,columns=features4)

In [479]:

from sklearn.preprocessing import RobustScaler
scaler = RobustScaler()
train_all30 = scaler.fit_transform(train00[featuresall.tolist()])
train_all300 = pd.DataFrame(train_all30,columns=featuresall)


In [481]:
train_all300[['updrs_1','updrs_2','updrs_3','updrs_4','upd23b_clinical_state_on_medication_Off','upd23b_clinical_state_on_medication_On']]=train00[['updrs_1_x','updrs_2','updrs_3','updrs_4','upd23b_clinical_state_on_medication_Off','upd23b_clinical_state_on_medication_On']].reset_index(drop=True)

In [485]:
features0=train_all300.columns.difference(['visit_id','patient_id','updrs_1','updrs_2','updrs_3','updrs_4'])

In [502]:
train_all300=train_all300.dropna()

In [503]:
train_all300.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2588 entries, 0 to 2614
Data columns (total 23 columns):
 #   Column                                   Non-Null Count  Dtype  
---  ------                                   --------------  -----  
 0   Abe_max                                  2588 non-null   float64
 1   Abe_mean                                 2588 non-null   float64
 2   Abe_min                                  2588 non-null   float64
 3   Abe_std                                  2588 non-null   float64
 4   NPX_max                                  2588 non-null   float64
 5   NPX_mean                                 2588 non-null   float64
 6   NPX_min                                  2588 non-null   float64
 7   NPX_std                                  2588 non-null   float64
 8   peptides_updrs_1_max                     2588 non-null   float64
 9   peptides_updrs_1_mean                    2588 non-null   float64
 10  peptides_updrs_1_min                     2588 no

In [325]:
proteins_test[['patient_id']].value_counts()

patient_id
50423         227
3342          226
dtype: int64

In [494]:
x=train_all300[features0].drop(columns=['Abe_std','Abe_min','peptides_updrs_1_max','peptides_updrs_1_mean','peptides_updrs_1_min','peptides_updrs_1_std','proteins_updrs_1_max','proteins_updrs_1_mean','proteins_updrs_1_min','proteins_updrs_1_std'])
x

Abe_max       Abe_mean       NPX_max       NPX_mean      NPX_min  \
0     2.837353e+07  104329.241132  7.973326e+07  471469.543739  1497.876926   
1     0.000000e+00       0.000000  0.000000e+00       0.000000     0.000000   
2     6.270034e+06   41393.933989  3.706626e+07  232999.893456   585.266926   
3     0.000000e+00       0.000000  0.000000e+00       0.000000     0.000000   
4     1.518583e+07   96710.757681  7.300126e+07  436568.998720  1672.686926   
...            ...            ...           ...            ...          ...   
2610 -6.345466e+06   25586.791502 -3.858735e+06  208352.333984  1217.236926   
2611  0.000000e+00       0.000000  0.000000e+00       0.000000     0.000000   
2612  0.000000e+00       0.000000  0.000000e+00       0.000000     0.000000   
2613  0.000000e+00       0.000000  0.000000e+00       0.000000     0.000000   
2614  0.000000e+00       0.000000  0.000000e+00       0.000000     0.000000   

           NPX_std  upd23b_clinical_state_on_medication_Off  \
0     4.848798e+06                                        1   
1     0.000000e+00                                        1   
2     2.036488e+06                                        1   
3     0.000000e+00                                        0   
4     4.248540e+06                                        0   
...            ...                                      ...   
2610 -1.600183e+05                                        1   
2611  0.000000e+00                                        1   
2612  0.000000e+00                                        1   
2613  0.000000e+00                                        1   
2614  0.000000e+00                                        1   

      upd23b_clinical_state_on_medication_On  visit_month  
0                                          0        -0.64  
1                                          0        -0.56  
2                                          0        -0.48  
3                                          1        -0.40  
4                                          1        -0.32  
...                                      ...          ...  
2610                                       0         0.64  
2611                                       0         0.80  
2612                                       0         0.96  
2613                                       0         1.28  
2614                                       0         1.60  

[2615 rows x 9 columns]

In [506]:
import numpy as np
import pandas as pd
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

from sklearn.metrics import make_scorer
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb
import lightgbm as lgb
from catboost import CatBoostRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import GridSearchCV, KFold
from sklearn.metrics import make_scorer
import numpy as np
import warnings
warnings.filterwarnings('ignore')
x=train_all300[features0]
y=train_all300.updrs_2
X_train,x_val,y_train,y_val = train_test_split(x,y, test_size=0.2,shuffle=True,random_state=100)
# 모델 리스트와 그리드 서치에 사용할 하이퍼파라미터 리스트
models = [XGBRegressor(), CatBoostRegressor(), LGBMRegressor(), RandomForestRegressor()]
params = [{'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'max_depth': [3, 5, 7], 'min_samples_split': [2, 4, 8]}]
# SMAPE를 Scikit-learn에서 사용 가능한 형태로 변환하는 함수
def smape(y_true, y_pred):
    smap = np.zeros(len(y_true))
    
    num = np.abs(y_true - y_pred)
    dem = ((np.abs(y_true) + np.abs(y_pred)) / 2)
    
    pos_ind = (y_true!=0)|(y_pred!=0)
    smap[pos_ind] = num[pos_ind] / dem[pos_ind]
    
    return 100 * np.mean(smap)
scorer = make_scorer(smape, greater_is_better=False)
# 각 모델에 대한 그리드 서치와 OOF 예측 수행
models_2 = {}
oof_preds2 = {}
cv = KFold(n_splits=5, shuffle=True, random_state=123)
for i, model in enumerate(models):
    grid_search = GridSearchCV(model, params[i], scoring=scorer, cv=cv, n_jobs=-1,verbose=0)
    grid_search.fit(X_train, y_train)
    best_model2 = grid_search.best_estimator_
    models_2[i] = best_model2
    oof_pred = np.zeros(len(y_train))
    for fold_idx, (trn_idx, val_idx) in enumerate(cv.split(X_train, y_train)):
        trn_X, trn_y = X_train.iloc[trn_idx], y_train.iloc[trn_idx]
        val_X, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
        best_model2.fit(trn_X, trn_y)
        oof_pred[val_idx] = best_model2.predict(val_X)
    oof_preds2[i] = oof_pred
    print("Best Parameters:", grid_search.best_params_)
    print("Best SMAPE:", -grid_search.best_score_)

Best Parameters: {'learning_rate': 0.01, 'max_depth': 3, 'n_estimators': 500}
Best SMAPE: 88.42065544411491
0:	learn: 6.3243432	total: 996us	remaining: 98.7ms
1:	learn: 6.3170956	total: 1.81ms	remaining: 88.7ms
2:	learn: 6.3098887	total: 2.6ms	remaining: 84ms
3:	learn: 6.3028875	total: 3.44ms	remaining: 82.7ms
4:	learn: 6.2960092	total: 4.25ms	remaining: 80.8ms
5:	learn: 6.2890616	total: 5.04ms	remaining: 79ms
6:	learn: 6.2832508	total: 5.79ms	remaining: 77ms
7:	learn: 6.2769290	total: 6.64ms	remaining: 76.4ms
8:	learn: 6.2706583	total: 7.43ms	remaining: 75.2ms
9:	learn: 6.2645008	total: 8.33ms	remaining: 75ms
10:	learn: 6.2585315	total: 9.15ms	remaining: 74.1ms
11:	learn: 6.2524960	total: 9.96ms	remaining: 73.1ms
12:	learn: 6.2470787	total: 10.8ms	remaining: 72ms
13:	learn: 6.2417096	total: 11.6ms	remaining: 71.1ms
14:	learn: 6.2358687	total: 12.4ms	remaining: 70.3ms
15:	learn: 6.2299756	total: 13.2ms	remaining: 69.5ms
16:	learn: 6.2247743	total: 14ms	remaining: 68.6ms
17:	learn: 6.22

In [507]:
models_2

{0: XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.01, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=3, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=500, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=0, reg_alpha=0,
              reg_lambda=1, ...),
 1: <catboost.core.CatBoostRegressor at 0x7f360c7ed310>,
 2: LGBMRegressor(learning_rate=0.01, max_depth=5),
 3: RandomForestRegressor(max_depth=5, min_samples_split=4)}

In [ ]:
#ensemble_preds2 = np.mean(dfe, axis=1)
#train_all300['updrs_2'] = ensemble_preds2
#train_all300

from scipy.optimize import minimize
from sklearn.metrics import mean_squared_error

# 각 모델의 가중치 초기화
w0 = np.ones(len(dfe)) / len(dfe)

# 가중치 최적화 함수 정의
def objective(weights):
    # 예측값 가중합 계산
    y_pred = np.sum(weights.reshape(-1,1) * dfe, axis=0)
    # SMAPE 계산
    score = smape(y_train, y_pred)
    # 손실값 반환
    return score

# 최적화 알고리즘 적용
result = minimize(objective, w0, method='Nelder-Mead')

# 최적 가중치 출력
weights = result.x
print(weights)

# 가중합 예측값 계산
y_pred2 = np.sum(weights.reshape(-1,1) * dfe, axis=0)


In [508]:
import numpy as np
import pandas as pd
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

from sklearn.metrics import make_scorer
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb
import lightgbm as lgb
from catboost import CatBoostRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import GridSearchCV, KFold
from sklearn.metrics import make_scorer
import numpy as np
import warnings
warnings.filterwarnings('ignore')
x=train_all300[features0]
y=train_all300.updrs_3
X_train,x_val,y_train,y_val = train_test_split(x,y, test_size=0.2,shuffle=True,random_state=100)
# 모델 리스트와 그리드 서치에 사용할 하이퍼파라미터 리스트
models = [XGBRegressor(), CatBoostRegressor(), LGBMRegressor(), RandomForestRegressor()]
params = [{'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'max_depth': [3, 5, 7], 'min_samples_split': [2, 4, 8]}]
# SMAPE를 Scikit-learn에서 사용 가능한 형태로 변환하는 함수
def smape(y_true, y_pred):
    smap = np.zeros(len(y_true))
    
    num = np.abs(y_true - y_pred)
    dem = ((np.abs(y_true) + np.abs(y_pred)) / 2)
    
    pos_ind = (y_true!=0)|(y_pred!=0)
    smap[pos_ind] = num[pos_ind] / dem[pos_ind]
    
    return 100 * np.mean(smap)
scorer = make_scorer(smape, greater_is_better=False)
# 각 모델에 대한 그리드 서치와 OOF 예측 수행
models_3 = {}
oof_preds3 = {}
cv = KFold(n_splits=5, shuffle=True, random_state=123)
for i, model in enumerate(models):
    grid_search = GridSearchCV(model, params[i], scoring=scorer, cv=cv, n_jobs=-1,verbose=0)
    grid_search.fit(X_train, y_train)
    best_model3 = grid_search.best_estimator_
    models_3[i] = best_model3
    oof_pred = np.zeros(len(y_train))
    for fold_idx, (trn_idx, val_idx) in enumerate(cv.split(X_train, y_train)):
        trn_X, trn_y = X_train.iloc[trn_idx], y_train.iloc[trn_idx]
        val_X, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
        best_model3.fit(trn_X, trn_y)
        oof_pred[val_idx] = best_model3.predict(val_X)
    oof_preds3[i] = oof_pred
    print("Best Parameters:", grid_search.best_params_)
    print("Best SMAPE:", -grid_search.best_score_)

Best Parameters: {'learning_rate': 0.01, 'max_depth': 3, 'n_estimators': 500}
Best SMAPE: 77.62531281311502
0:	learn: 15.0878655	total: 1.64ms	remaining: 162ms
1:	learn: 15.0744678	total: 2.81ms	remaining: 138ms
2:	learn: 15.0616040	total: 3.91ms	remaining: 126ms
3:	learn: 15.0501416	total: 5ms	remaining: 120ms
4:	learn: 15.0377995	total: 6.27ms	remaining: 119ms
5:	learn: 15.0248349	total: 7.37ms	remaining: 116ms
6:	learn: 15.0107399	total: 8.35ms	remaining: 111ms
7:	learn: 14.9995647	total: 9.26ms	remaining: 106ms
8:	learn: 14.9880991	total: 10.1ms	remaining: 102ms
9:	learn: 14.9768980	total: 11.1ms	remaining: 99.5ms
10:	learn: 14.9663334	total: 12ms	remaining: 96.7ms
11:	learn: 14.9550046	total: 12.9ms	remaining: 94.6ms
12:	learn: 14.9446583	total: 13.9ms	remaining: 93.1ms
13:	learn: 14.9343974	total: 14.8ms	remaining: 90.8ms
14:	learn: 14.9243031	total: 15.7ms	remaining: 88.7ms
15:	learn: 14.9138474	total: 16.5ms	remaining: 86.8ms
16:	learn: 14.9040035	total: 17.5ms	remaining: 85.2m

In [ ]:
dfe3 = pd.DataFrame(oof_preds3)
dfe3

ensemble_preds3 = np.mean(dfe3, axis=1)
ensemble_preds3

0       22.598331
1       16.097430
2       12.449817
3       22.677792
4       13.194686
          ...    
2065    14.920331
2066    17.514768
2067    17.085302
2068    17.085302
2069    26.804134
Length: 2070, dtype: float64

In [510]:
import numpy as np
import pandas as pd
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

from sklearn.metrics import make_scorer
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb
import lightgbm as lgb
from catboost import CatBoostRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import GridSearchCV, KFold
from sklearn.metrics import make_scorer
import numpy as np
import warnings
warnings.filterwarnings('ignore')
x=train_all300[features0]
y=train_all300.updrs_1
X_train,x_val,y_train,y_val = train_test_split(x,y, test_size=0.2,shuffle=True,random_state=100)
# 모델 리스트와 그리드 서치에 사용할 하이퍼파라미터 리스트
models = [XGBRegressor(), CatBoostRegressor(), LGBMRegressor(), RandomForestRegressor()]
params = [{'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'max_depth': [3, 5, 7], 'min_samples_split': [2, 4, 8]}]
# SMAPE를 Scikit-learn에서 사용 가능한 형태로 변환하는 함수
def smape(y_true, y_pred):
    smap = np.zeros(len(y_true))
    
    num = np.abs(y_true - y_pred)
    dem = ((np.abs(y_true) + np.abs(y_pred)) / 2)
    
    pos_ind = (y_true!=0)|(y_pred!=0)
    smap[pos_ind] = num[pos_ind] / dem[pos_ind]
    
    return 100 * np.mean(smap)
scorer = make_scorer(smape, greater_is_better=False)
# 각 모델에 대한 그리드 서치와 OOF 예측 수행
models_1 = {}
oof_preds1 = {}
cv = KFold(n_splits=5, shuffle=True, random_state=123)
for i, model in enumerate(models):
    grid_search = GridSearchCV(model, params[i], scoring=scorer, cv=cv, n_jobs=-1,verbose=0)
    grid_search.fit(X_train, y_train)
    best_model1 = grid_search.best_estimator_
    models_1[i] = best_model1
    oof_pred = np.zeros(len(y_train))
    for fold_idx, (trn_idx, val_idx) in enumerate(cv.split(X_train, y_train)):
        trn_X, trn_y = X_train.iloc[trn_idx], y_train.iloc[trn_idx]
        val_X, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
        best_model1.fit(trn_X, trn_y)
        oof_pred[val_idx] = best_model1.predict(val_X)
    oof_preds1[i] = oof_pred
    print("Best Parameters:", grid_search.best_params_)
    print("Best SMAPE:", -grid_search.best_score_)

Best Parameters: {'learning_rate': 0.01, 'max_depth': 3, 'n_estimators': 300}
Best SMAPE: 64.27544346730008
0:	learn: 5.5588986	total: 873us	remaining: 86.4ms
1:	learn: 5.5524422	total: 1.73ms	remaining: 84.9ms
2:	learn: 5.5460757	total: 2.48ms	remaining: 80.2ms
3:	learn: 5.5396551	total: 3.19ms	remaining: 76.7ms
4:	learn: 5.5329910	total: 3.95ms	remaining: 75ms
5:	learn: 5.5262473	total: 4.79ms	remaining: 75ms
6:	learn: 5.5205121	total: 5.59ms	remaining: 74.2ms
7:	learn: 5.5144618	total: 6.37ms	remaining: 73.2ms
8:	learn: 5.5089176	total: 7.21ms	remaining: 72.9ms
9:	learn: 5.5038283	total: 8.18ms	remaining: 73.6ms
10:	learn: 5.4979337	total: 9.02ms	remaining: 73ms
11:	learn: 5.4920554	total: 9.85ms	remaining: 72.2ms
12:	learn: 5.4868506	total: 10.7ms	remaining: 71.5ms
13:	learn: 5.4815478	total: 11.6ms	remaining: 71ms
14:	learn: 5.4765082	total: 12.3ms	remaining: 69.9ms
15:	learn: 5.4708937	total: 13.2ms	remaining: 69.1ms
16:	learn: 5.4660907	total: 14ms	remaining: 68.2ms
17:	learn: 5

In [ ]:
dfe1 = pd.DataFrame(oof_preds1)
dfe1

ensemble_preds1 = np.mean(dfe1, axis=1)
ensemble_preds1

0       8.857894
1       5.769232
2       5.158626
3       9.097444
4       5.390556
          ...   
2065    5.402381
2066    5.889595
2067    5.478917
2068    5.478917
2069    9.928950
Length: 2070, dtype: float64

In [360]:
train_all300[['updrs_4']].value_counts().sort_values()

updrs_4
20.0         1
16.0         1
14.0         2
11.0         2
12.0         3
13.0         4
10.0         5
9.0          8
8.0         11
7.0         15
6.0         17
1.0         23
2.0         29
5.0         33
4.0         35
3.0         35
0.0        834
dtype: int64

In [369]:
import numpy as np
import pandas as pd
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

from sklearn.metrics import make_scorer
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb
import lightgbm as lgb
from catboost import CatBoostRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import GridSearchCV, KFold
from sklearn.metrics import make_scorer
import numpy as np
import warnings
warnings.filterwarnings('ignore')
x=train_all300[features0]
y=train_all300.updrs_4
X_train,x_val,y_train,y_val = train_test_split(x,y, test_size=0.2,shuffle=True,random_state=100)
# 모델 리스트와 그리드 서치에 사용할 하이퍼파라미터 리스트
models = [XGBRegressor(), CatBoostRegressor(), LGBMRegressor(), RandomForestRegressor()]
params = [{'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'learning_rate': [0.01, 0.05, 0.1], 'max_depth': [3, 5, 7]},
          {'n_estimators': [100, 300, 500], 'max_depth': [3, 5, 7], 'min_samples_split': [2, 4, 8]}]
# SMAPE를 Scikit-learn에서 사용 가능한 형태로 변환하는 함수
def smape(y_true, y_pred):
    smap = np.zeros(len(y_true))
    
    num = np.abs(y_true - y_pred)
    dem = ((np.abs(y_true) + np.abs(y_pred)) / 2)
    
    pos_ind = (y_true!=0)|(y_pred!=0)
    smap[pos_ind] = num[pos_ind] / dem[pos_ind]
    
    return 100 * np.mean(smap)
scorer = make_scorer(smape, greater_is_better=False)
# 각 모델에 대한 그리드 서치와 OOF 예측 수행
models_4 = {}
oof_preds4 = {}
cv = KFold(n_splits=5, shuffle=True, random_state=123)
for i, model in enumerate(models):
    grid_search = GridSearchCV(model, params[i], scoring=scorer, cv=cv, n_jobs=-1,verbose=0)
    grid_search.fit(X_train, y_train)
    best_model4 = grid_search.best_estimator_
    models_4[i] = best_model4
    oof_pred = np.zeros(len(y_train))
    for fold_idx, (trn_idx, val_idx) in enumerate(cv.split(X_train, y_train)):
        trn_X, trn_y = X_train.iloc[trn_idx], y_train.iloc[trn_idx]
        val_X, val_y = X_train.iloc[val_idx], y_train.iloc[val_idx]
        best_model4.fit(trn_X, trn_y)
        oof_pred[val_idx] = best_model4.predict(val_X)
    oof_preds4[i] = oof_pred
    print("Best Parameters:", grid_search.best_params_)
    print("Best SMAPE:", -grid_search.best_score_)

Best Parameters: {'learning_rate': 0.01, 'max_depth': 3, 'n_estimators': 500}
Best SMAPE: 177.38071198512168
0:	learn: 2.4863304	total: 660us	remaining: 65.4ms
1:	learn: 2.4819120	total: 1.1ms	remaining: 53.9ms
2:	learn: 2.4772518	total: 1.6ms	remaining: 51.7ms
3:	learn: 2.4731332	total: 2.04ms	remaining: 49ms
4:	learn: 2.4689499	total: 2.47ms	remaining: 47ms
5:	learn: 2.4644915	total: 2.87ms	remaining: 44.9ms
6:	learn: 2.4602313	total: 3.28ms	remaining: 43.5ms
7:	learn: 2.4565773	total: 3.55ms	remaining: 40.8ms
8:	learn: 2.4523059	total: 3.97ms	remaining: 40.2ms
9:	learn: 2.4479660	total: 4.35ms	remaining: 39.2ms
10:	learn: 2.4438707	total: 4.76ms	remaining: 38.5ms
11:	learn: 2.4397934	total: 5.17ms	remaining: 37.9ms
12:	learn: 2.4359010	total: 5.6ms	remaining: 37.5ms
13:	learn: 2.4324578	total: 6ms	remaining: 36.9ms
14:	learn: 2.4284177	total: 6.42ms	remaining: 36.4ms
15:	learn: 2.4245044	total: 6.81ms	remaining: 35.8ms
16:	learn: 2.4208187	total: 7.2ms	remaining: 35.1ms
17:	learn: 2

In [375]:
for i in oof_preds4: 
    if i < 4:
        i=0
oof_preds4



TypeError: 'int' object is not iterable

In [331]:
peptides_test

visit_id  visit_month  patient_id UniProt  \
0     50423_0            0       50423  O00391   
1     50423_0            0       50423  O00391   
2     50423_0            0       50423  O00533   
3     50423_0            0       50423  O00533   
4     50423_0            0       50423  O00533   
...       ...          ...         ...     ...   
2052   3342_6            6        3342  Q9Y646   
2053   3342_6            6        3342  Q9Y646   
2054   3342_6            6        3342  Q9Y646   
2055   3342_6            6        3342  Q9Y6R7   
2056   3342_6            6        3342  Q9Y6R7   

                                     Peptide  PeptideAbundance  group_key  
0                       AHFSPSNIILDFPAAGSAAR          22226.30          0  
1                              NEQEQPLGQWHLS          10901.60          0  
2                                GNPEPTFSWTK          51499.40          0  
3                            IEIPSSVQQVPTIIK         125492.00          0  
4     KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK          23174.20          0  
...                                      ...               ...        ...  
2052                              AIINLAVYGK           6142.76          6  
2053                             LALLVDTVGPR          23602.30          6  
2054                               VGALASLIR          21728.20          6  
2055        AGC(UniMod_4)VAESTAVC(UniMod_4)R           4253.17          6  
2056                          GATTSPGVYELSSR          10371.30          6  

[2057 rows x 7 columns]

In [332]:
proteins_t2=proteins_test.drop(columns=['patient_id','UniProt'])
peptides_t2=peptides_test.drop(columns=['patient_id','UniProt','Peptide'])
p_t1=peptides_t2.groupby('visit_id').agg({'PeptideAbundance': ['min','max','mean']}).reset_index()
pr_t2=proteins_t2.groupby('visit_id').agg({'NPX':['min','max','mean']}).reset_index()
p_t1.columns=['visit_id','pa_min','pa_max','pa_mean']
pr_t2.columns=['visit_id','NPX_min','NPX_max','NPX_mean']

In [333]:
proteins_t2[['visit_id']].value_counts()

visit_id
50423_0     227
3342_6      226
dtype: int64

In [334]:
peptides_test[['visit_id']].value_counts()

visit_id
3342_6      1036
50423_0     1021
dtype: int64

In [335]:
p_t1

visit_id    pa_min      pa_max        pa_mean
0   3342_6  1391.470  34270800.0  581048.801390
1  50423_0   886.086  55622600.0  725015.018899

In [336]:
pr_t2

visit_id  NPX_min      NPX_max      NPX_mean
0   3342_6  2853.12  295860000.0  2.663569e+06
1  50423_0  2287.04  439208000.0  3.260972e+06

In [351]:
best_model2.predict(testall)

ValueError: X has 8 features, but RandomForestRegressor is expecting 9 features as input.

In [348]:
testall=pd.merge(p_t1,pr_t2,on='visit_id')

In [349]:
testall['month']=[6,0]

In [350]:
testall

visit_id    pa_min      pa_max        pa_mean  NPX_min      NPX_max  \
0   3342_6  1391.470  34270800.0  581048.801390  2853.12  295860000.0   
1  50423_0   886.086  55622600.0  725015.018899  2287.04  439208000.0   

       NPX_mean  month  
0  2.663569e+06      6  
1  3.260972e+06      0

In [342]:
import amp_pd_peptide
env = amp_pd_peptide.make_env()
iter_test = env.iter_test()


In [355]:
test

visit_id  visit_month  patient_id updrs_test           row_id  group_key
0    3342_0            0        3342    updrs_1   3342_0_updrs_1          0
1    3342_0            0        3342    updrs_2   3342_0_updrs_2          0
2    3342_0            0        3342    updrs_3   3342_0_updrs_3          0
3    3342_0            0        3342    updrs_4   3342_0_updrs_4          0
4   50423_0            0       50423    updrs_1  50423_0_updrs_1          0
5   50423_0            0       50423    updrs_2  50423_0_updrs_2          0
6   50423_0            0       50423    updrs_3  50423_0_updrs_3          0
7   50423_0            0       50423    updrs_4  50423_0_updrs_4          0
8    3342_6            6        3342    updrs_1   3342_6_updrs_1          6
9    3342_6            6        3342    updrs_2   3342_6_updrs_2          6
10   3342_6            6        3342    updrs_3   3342_6_updrs_3          6
11   3342_6            6        3342    updrs_4   3342_6_updrs_4          6
12  50423_6            6       50423    updrs_1  50423_6_updrs_1          6
13  50423_6            6       50423    updrs_2  50423_6_updrs_2          6
14  50423_6            6       50423    updrs_3  50423_6_updrs_3          6
15  50423_6            6       50423    updrs_4  50423_6_updrs_4          6

In [512]:
updrs_3_pred = {}
up3 = clinical[['visit_month','updrs_3']].drop_duplicates(['visit_month','updrs_3'])
updrs_3_pred = dict(zip(up3.visit_month, up3.updrs_3))
updrs_3_pred

{0: 27.0,
 3: 31.0,
 6: 41.0,
 9: 31.0,
 12: 45.0,
 18: 14.0,
 24: 41.0,
 30: 38.0,
 36: 44.0,
 42: 48.0,
 48: 8.0,
 54: 57.0,
 60: 44.0,
 72: 51.0,
 84: 41.0,
 96: 5.0,
 108: 35.0}

In [514]:
import amp_pd_peptide

iter_test = env.iter_test()

In [515]:
def map_test(x):
    updrs = x.split('_')[2] + '_' + x.split('_')[3]
    month = int(x.split('_plus_')[1].split('_')[0])
    visit_id = x.split('_')[0] + '_' + x.split('_')[1]
    # set all predictions 0 where updrs equals 'updrs_4'
    if updrs=='updrs_3':
#         rating = updrs_3_pred[month]
        rating = df[df.visit_id == visit_id]['pred2'].values[0]
    elif updrs=='updrs_4':
        rating = 0
    elif updrs =='updrs_1':
        rating = df[df.visit_id == visit_id]['pred0'].values[0]
    else:
        rating = df[df.visit_id == visit_id]['pred1'].values[0]
    return rating

counter = 0

In [521]:
# The API will deliver four dataframes in this specific order:
for (test, test_peptides, test_proteins, sample_submission) in iter_test:
    df = test[['visit_id']].drop_duplicates('visit_id')
    pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
    pred_0['visit_month']=[0,0]
    pred_0['upd23b_clinical_state_on_medication_Off']=[1,0]
    pred_0['upd23b_clinical_state_on_medication_On']=[0,1]
    pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
    df['pred0'] = np.ceil(pred_0)
    pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 1)
    pred_1['visit_month']=[6,6]
    pred_1['upd23b_clinical_state_on_medication_Off']=[1,0]
    pred_1['upd23b_clinical_state_on_medication_On']=[0,1]
    pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
    df['pred1'] = np.ceil(pred_1)
    
    pred_2 = features(df[['visit_id']], test_proteins, test_peptides, 2)
    pred_2['visit_month']=[12,12]
    pred_2['upd23b_clinical_state_on_medication_Off']=[1,0]
    pred_2['upd23b_clinical_state_on_medication_On']=[0,1]
    pred_2 = best_model3.predict(pred_2.drop(columns = ['visit_id'], axis = 1))
    df['pred2'] = np.ceil(pred_2)
    
    sample_submission['rating'] = sample_submission['prediction_id'].apply(map_test)
    env.predict(sample_submission)
    
    if counter == 0:
        display(test)
        display(sample_submission)
        
    counter += 1
    

You must call `predict()` successfully before you can continue with `iter_test()`


TypeError: cannot unpack non-iterable NoneType object

In [537]:
df = test[['visit_id']].drop_duplicates('visit_id')
pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_0['visit_month']=[0,0]
pred_0['upd23b_clinical_state_on_medication_Off']=[1,0]
pred_0['upd23b_clinical_state_on_medication_On']=[0,1]
pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
df['pred0'] = np.ceil(pred_0)

In [541]:
pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 1)
pred_1['visit_month']=[0,0]
pred_1['upd23b_clinical_state_on_medication_Off']=[1,0]
pred_1['upd23b_clinical_state_on_medication_On']=[0,1]
pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
df['pred1'] = np.ceil(pred_1)

In [544]:
df

visit_id  pred0  pred1
0   3342_0   11.0    9.0
4  50423_0   10.0   10.0

array([[1.71028866e+08, 1.39197857e+06, 1.81037337e+05, ...,
        1.17924157e+01, 2.25843128e-01, 2.40000000e+01],
       [1.42655331e+08, 1.28764933e+06, 1.72738345e+04, ...,
        1.17111163e+01, 2.17054060e-01, 1.36500000e+02],
       [1.48925366e+08, 1.32904327e+06, 1.21774015e+05, ...,
        1.17924157e+01, 2.26111346e-01, 2.49000000e+02],
       ...,
       [1.42655331e+08, 1.28764933e+06, 1.72738345e+04, ...,
        1.17111163e+01, 2.17054060e-01, 2.27400000e+03],
       [1.42655331e+08, 1.28764933e+06, 1.72738345e+04, ...,
        1.17111163e+01, 2.17054060e-01, 2.72400000e+03],
       [1.42655331e+08, 1.28764933e+06, 1.72738345e+04, ...,
        1.17111163e+01, 2.17054060e-01, 3.17400000e+03]])

In [ ]:

from sklearn.preprocessing import RobustScaler
scaler = RobustScaler()
train_all30 = scaler.fit_transform(train00[featuresall.tolist()])
train_all300 = pd.DataFrame(train_all30,columns=featuresall)

In [528]:
pd.DataFrame(a,columns=featuresall)

Abe_max      Abe_mean        Abe_min       Abe_std       NPX_max  \
0     1.710289e+08  1.391979e+06  181037.337357  7.553218e+06  7.007447e+08   
1     1.426553e+08  1.287649e+06   17273.834487  6.642822e+06  6.210115e+08   
2     1.489254e+08  1.329043e+06  121774.014661  6.813270e+06  6.580777e+08   
3     1.426553e+08  1.287649e+06   17273.834487  6.642822e+06  6.210115e+08   
4     1.578412e+08  1.384360e+06  237095.326236  7.203947e+06  6.940127e+08   
...            ...           ...            ...           ...           ...   
2610  1.363099e+08  1.313236e+06   10063.669879  6.565109e+06  6.171527e+08   
2611  1.426553e+08  1.287649e+06   17273.834487  6.642822e+06  6.210115e+08   
2612  1.426553e+08  1.287649e+06   17273.834487  6.642822e+06  6.210115e+08   
2613  1.426553e+08  1.287649e+06   17273.834487  6.642822e+06  6.210115e+08   
2614  1.426553e+08  1.287649e+06   17273.834487  6.642822e+06  6.210115e+08   

          NPX_mean      NPX_min       NPX_std  peptides_updrs_1_max  \
0     5.889547e+06  5337.543074  4.860519e+07             13.837826   
1     5.418078e+06  3839.666148  4.375640e+07             13.863554   
2     5.651078e+06  4424.933074  4.579288e+07             13.893802   
3     5.418078e+06  3839.666148  4.375640e+07             13.863554   
4     5.854647e+06  5512.353074  4.800494e+07             13.893802   
...            ...          ...           ...                   ...   
2610  5.626430e+06  5056.903074  4.359638e+07             13.837826   
2611  5.418078e+06  3839.666148  4.375640e+07             13.863554   
2612  5.418078e+06  3839.666148  4.375640e+07             13.863554   
2613  5.418078e+06  3839.666148  4.375640e+07             13.863554   
2614  5.418078e+06  3839.666148  4.375640e+07             13.863554   

      peptides_updrs_1_mean  peptides_updrs_1_min  peptides_updrs_1_std  \
0                  6.507878              5.797043              0.217029   
1                  6.507879              5.797073              0.207726   
2                  6.507878              5.797043              0.214744   
3                  6.507879              5.797073              0.207726   
4                  6.507878              5.796660              0.220663   
...                     ...                   ...                   ...   
2610               6.507878              5.796660              0.215030   
2611               6.507879              5.797073              0.207726   
2612               6.507879              5.797073              0.207726   
2613               6.507879              5.797073              0.207726   
2614               6.507879              5.797073              0.207726   

      proteins_updrs_1_max  proteins_updrs_1_mean  proteins_updrs_1_min  \
0                 7.170380              13.038187             11.792416   
1                 7.167932              13.045371             11.711116   
2                 7.170380              13.039170             11.792416   
3                 7.167932              13.045371             11.711116   
4                 7.164522              13.032508             11.545066   
...                    ...                    ...                   ...   
2610              7.164522              13.036095             11.545066   
2611              7.167932              13.045371             11.711116   
2612              7.167932              13.045371             11.711116   
2613              7.167932              13.045371             11.711116   
2614              7.167932              13.045371             11.711116   

      proteins_updrs_1_std  visit_month  
0                 0.225843         24.0  
1                 0.217054        136.5  
2                 0.226111        249.0  
3                 0.217054        361.5  
4                 0.236445        474.0  
...                    ...          ...  
2610              0.232827       1824.0  
2611              0.217054       2049.0  
2612              0.217054   

In [ ]:
df = test[['visit_id']].drop_duplicates('visit_id')
    pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
    pred_0['visit_month']=[0,0]
    pred_0['upd23b_clinical_state_on_medication_Off']=[1,0]
    pred_0['upd23b_clinical_state_on_medication_On']=[0,1]
    pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
    df['pred0'] = np.ceil(pred_0)
    pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 1)
    pred_1['visit_month']=[6,6]
    pred_1['upd23b_clinical_state_on_medication_Off']=[1,0]
    pred_1['upd23b_clinical_state_on_medication_On']=[0,1]
    pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
    df['pred1'] = np.ceil(pred_1)
    
    pred_2 = features(df[['visit_id']], test_proteins, test_peptides, 2)
    pred_2['visit_month']=[12,12]
    pred_2['upd23b_clinical_state_on_medication_Off']=[1,0]
    pred_2['upd23b_clinical_state_on_medication_On']=[0,1]
    pred_2 = best_model3.predict(pred_2.drop(columns = ['visit_id'], axis = 1))
    df['pred2'] = np.ceil(pred_2)
    
    sample_submission['rating'] = sample_submission['prediction_id'].apply(map_test)
    env.predict(sample_submission)

In [ ]:

for (test, test_peptides, test_proteins, sample_submission) in iter_test:
    sample_prediction_df['rating'] = np.arange(len(sample_prediction))  # make your predictions here
    env.predict(sample_prediction_df)

In [585]:
test[['visit_id']].drop_duplicates('visit_id')
pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_0['visit_month']=[0,0]
pred_0['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_0['upd23b_clinical_state_on_medication_On']=[0,0]
pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
df['pred0'] = np.ceil(pred_0-4)
pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_0['visit_month']=[6,6]
pred_0['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_0['upd23b_clinical_state_on_medication_On']=[0,0]
pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
df['pred1'] = np.ceil(pred_0-4)
pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_0['visit_month']=[12,12]
pred_0['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_0['upd23b_clinical_state_on_medication_On']=[0,0]
pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
df['pred02'] = np.ceil(pred_0-4)
pred_0 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_0['visit_month']=[24,24]
pred_0['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_0['upd23b_clinical_state_on_medication_On']=[0,0]
pred_0 = best_model1.predict(pred_0.drop(columns = ['visit_id'], axis = 1))
df['pred03'] = np.ceil(pred_0-4)
df

visit_id  pred0  pred1  pred02  pred03  pred04  pred5  pred6  pred7  pred8  \
0   3342_0    7.0    6.0     6.0     6.0     6.0    9.0    7.0    7.0    7.0   
4  50423_0    7.0    6.0     6.0     6.0     6.0    9.0    7.0    7.0    7.0   

   pred9  pred10  pred11  pred12  pred13  pred14  pred15  pred16  pred01  
0   24.0    22.0    22.0    22.0       0       0       0       0     6.0  
4   24.0    22.0    22.0    22.0       0       0       0       0     6.0

In [586]:
test[['visit_id']].drop_duplicates('visit_id')
pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_1['visit_month']=[0,0]
pred_1['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_1['upd23b_clinical_state_on_medication_On']=[0,0]
pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
df['pred04'] = np.ceil(pred_1)
pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_1['visit_month']=[6,6]
pred_1['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_1['upd23b_clinical_state_on_medication_On']=[0,0]
pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
df['pred5'] = np.ceil(pred_1)
pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_1['visit_month']=[12,12]
pred_1['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_1['upd23b_clinical_state_on_medication_On']=[0,0]
pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
df['pred6'] = np.ceil(pred_1)
pred_1 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_1['visit_month']=[24,24]
pred_1['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_1['upd23b_clinical_state_on_medication_On']=[0,0]
pred_1 = best_model2.predict(pred_1.drop(columns = ['visit_id'], axis = 1))
df['pred7'] = np.ceil(pred_1)
df

visit_id  pred0  pred1  pred02  pred03  pred04  pred5  pred6  pred7  pred8  \
0   3342_0    7.0    6.0     6.0     6.0     9.0    7.0    7.0    7.0    7.0   
4  50423_0    7.0    6.0     6.0     6.0     9.0    7.0    7.0    7.0    7.0   

   pred9  pred10  pred11  pred12  pred13  pred14  pred15  pred16  pred01  
0   24.0    22.0    22.0    22.0       0       0       0       0     6.0  
4   24.0    22.0    22.0    22.0       0       0       0       0     6.0

In [587]:
test[['visit_id']].drop_duplicates('visit_id')
pred_2 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_2['visit_month']=[0,0]
pred_2['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_2['upd23b_clinical_state_on_medication_On']=[0,0]
pred_2 = best_model3.predict(pred_2.drop(columns = ['visit_id'], axis = 1))
df['pred8'] = np.ceil(pred_2)
pred_2 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_2['visit_month']=[6,6]
pred_2['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_2['upd23b_clinical_state_on_medication_On']=[0,0]
pred_2 = best_model3.predict(pred_2.drop(columns = ['visit_id'], axis = 1))
df['pred9'] = np.ceil(pred_2)
pred_2 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_2['visit_month']=[12,12]
pred_2['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_2['upd23b_clinical_state_on_medication_On']=[0,0]
pred_2 = best_model3.predict(pred_2.drop(columns = ['visit_id'], axis = 1))
df['pred10'] = np.ceil(pred_2)
pred_2 = features(df[['visit_id']], test_proteins, test_peptides, 0)
pred_2['visit_month']=[24,24]
pred_2['upd23b_clinical_state_on_medication_Off']=[1,1]
pred_2['upd23b_clinical_state_on_medication_On']=[0,0]
pred_2 = best_model3.predict(pred_2.drop(columns = ['visit_id'], axis = 1))
df['pred11'] = np.ceil(pred_2)
df

visit_id  pred0  pred1  pred02  pred03  pred04  pred5  pred6  pred7  pred8  \
0   3342_0    7.0    6.0     6.0     6.0     9.0    7.0    7.0    7.0   24.0   
4  50423_0    7.0    6.0     6.0     6.0     9.0    7.0    7.0    7.0   24.0   

   pred9  pred10  pred11  pred12  pred13  pred14  pred15  pred16  pred01  
0   22.0    22.0    22.0    22.0       0       0       0       0     6.0  
4   22.0    22.0    22.0    22.0       0       0       0       0     6.0

In [588]:
df['pred12'] = [0,0]
df['pred13'] = [0,0]
df['pred14'] = [0,0]
df['pred15'] = [0,0]
df

visit_id  pred0  pred1  pred02  pred03  pred04  pred5  pred6  pred7  pred8  \
0   3342_0    7.0    6.0     6.0     6.0     9.0    7.0    7.0    7.0   24.0   
4  50423_0    7.0    6.0     6.0     6.0     9.0    7.0    7.0    7.0   24.0   

   pred9  pred10  pred11  pred12  pred13  pred14  pred15  pred16  pred01  
0   22.0    22.0    22.0       0       0       0       0       0     6.0  
4   22.0    22.0    22.0       0       0       0       0       0     6.0

In [591]:
sssss=pd.DataFrame({'prediction_id':sample_submission['prediction_id'],'rating':[7,6,6,6,9,7,7,7,24,22,22,22,0,0,0,0,7,6,6,6,9,7,7,7,24,22,22,22,0,0,0,0]})

In [595]:
import amp_pd_peptide
   # initialize the environment
    # an iterator which loops over the test files
for (test, test_peptides, test_proteins, sample_submission) in iter_test:
    sample_submission['rating'] = sssss['rating']
    env.predict(sample_submission)   # register your predictions

In [562]:
def map_test(x):
    updrs = x.split('_')[2] + '_' + x.split('_')[3]
    month = int(x.split('_plus_')[1].split('_')[0])
    visit_id = x.split('_')[0] + '_' + x.split('_')[1]
    # set all predictions 0 where updrs equals 'updrs_4'
    if updrs=='updrs_3':
#         rating = updrs_3_pred[month]
        rating = df[df.visit_id == visit_id]['pred2'].values[0]
    elif updrs=='updrs_4':
        rating = 0
    elif updrs =='updrs_1':
        rating = df[df.visit_id == visit_id]['pred0'].values[0]
    else:
        rating = df[df.visit_id == visit_id]['pred1'].values[0]
    return rating

prediction_id  rating
0     3342_0_updrs_1_plus_0_months       0
1     3342_0_updrs_1_plus_6_months       0
2    3342_0_updrs_1_plus_12_months       0
3    3342_0_updrs_1_plus_24_months       0
4     3342_0_updrs_2_plus_0_months       0
5     3342_0_updrs_2_plus_6_months       0
6    3342_0_updrs_2_plus_12_months       0
7    3342_0_updrs_2_plus_24_months       0
8     3342_0_updrs_3_plus_0_months       0
9     3342_0_updrs_3_plus_6_months       0
10   3342_0_updrs_3_plus_12_months       0
11   3342_0_updrs_3_plus_24_months       0
12    3342_0_updrs_4_plus_0_months       0
13    3342_0_updrs_4_plus_6_months       0
14   3342_0_updrs_4_plus_12_months       0
15   3342_0_updrs_4_plus_24_months       0
16   50423_0_updrs_1_plus_0_months       0
17   50423_0_updrs_1_plus_6_months       0
18  50423_0_updrs_1_plus_12_months       0
19  50423_0_updrs_1_plus_24_months       0
20   50423_0_updrs_2_plus_0_months       0
21   50423_0_updrs_2_plus_6_months       0
22  50423_0_updrs_2_plus_12_months       0
23  50423_0_updrs_2_plus_24_months       0
24   50423_0_updrs_3_plus_0_months       0
25   50423_0_updrs_3_plus_6_months       0
26  50423_0_updrs_3_plus_12_months       0
27  50423_0_updrs_3_plus_24_months       0
28   50423_0_updrs_4_plus_0_months       0
29   50423_0_updrs_4_plus_6_months       0
30  50423_0_updrs_4_plus_12_months       0
31  50423_0_updrs_4_plus_24_months       0

In [577]:
a=pd.concat([df.iloc[0,1:],df.iloc[0,2:]]).tolist()

In [580]:
7.0	6.0	6.0	6.0	9.0	7.0	7.0	7.0	24.0	22.0	22.0	22.0	0	0	0	0	0	6.0

[11.0,
 9.0,
 10.0,
 10.0,
 10.0,
 9.0,
 7.0,
 7.0,
 7.0,
 24.0,
 22.0,
 22.0,
 22.0,
 0,
 0,
 0,
 0,
 9.0,
 10.0,
 10.0,
 10.0,
 9.0,
 7.0,
 7.0,
 7.0,
 24.0,
 22.0,
 22.0,
 22.0,
 0,
 0,
 0,
 0]